In [8]:
import os
from dotenv import load_dotenv
from googleapiclient.discovery import build

load_dotenv() #.env dosyasini yüklüyor, API key'leri yüklüyor.

# API Key ve kanal adı
api_key = os.getenv("YOUTUBE_API_KEY")
channel_name = 'TelekomHilfe-Videos'

def get_channel_id(api_key, channel_name):
    youtube = build('youtube', 'v3', developerKey=api_key)
    
    request = youtube.search().list(
        part='snippet',
        q=channel_name,
        type='channel',
        maxResults=1
    )
    response = request.execute()
    
    # Kanal ID'sini döndür
    if response['items']:
        channel_id = response['items'][0]['id']['channelId']
        return channel_id
    else:
        return None

channel_id = get_channel_id(api_key, channel_name)
print(f'Channel ID: {channel_id}')


Channel ID: UC0YoG8q-PWNERhe_h5l8uPw


## Youtube videolarinda transcript varsa onlari aliyor Youtube API'dan, ses üzerinden ilerlemiyor.

In [28]:
import os
import googleapiclient.discovery
from youtube_transcript_api import YouTubeTranscriptApi
from youtube_transcript_api.formatters import SRTFormatter
from pathlib import Path

# API anahtarınızı ve kanal ID'sini girin
API_KEY = os.getenv("YOUTUBE_API_KEY")
CHANNEL_ID = 'UC0YoG8q-PWNERhe_h5l8uPw'
OUTPUT_DIR = 'transcripts'
SUMMARY_FILE = 'summary.txt'

# YouTube Data API istemcisi oluşturma
def get_youtube_service():
    return googleapiclient.discovery.build('youtube', 'v3', developerKey=API_KEY)

# Kanalın tüm video ID'lerini alma
def get_channel_video_ids(youtube, channel_id):
    video_ids = []
    request = youtube.playlistItems().list(
        part='contentDetails,snippet',
        playlistId=f'UU{channel_id[2:]}',  # Kanalın uploads listesinin playlist ID'si
        maxResults=50
    )
    response = request.execute()
    
    while response:
        for item in response['items']:
            video_ids.append({
                'videoId': item['contentDetails']['videoId'],
                'title': item['snippet']['title']
            })
        
        if 'nextPageToken' in response:
            request = youtube.playlistItems().list(
                part='contentDetails,snippet',
                playlistId=f'UU{channel_id[2:]}',
                maxResults=50,
                pageToken=response['nextPageToken']
            )
            response = request.execute()
        else:
            break
    
    return video_ids

# Video ID'sinden transkripti al
def get_video_transcript(video_id):
    try:
        transcript = YouTubeTranscriptApi.get_transcript(video_id, languages=['de'])
        return transcript
    except Exception as e:
        print(f"Error retrieving transcript for video {video_id}: {e}")
        return None

# Transkripti dosyaya yazma
def save_transcript_to_file(video_id, title, transcript):
    if transcript:
        formatter = SRTFormatter()
        srt_transcript = formatter.format_transcript(transcript)
        filename = f"{video_id}.srt"
        file_path = os.path.join(OUTPUT_DIR, filename)
        video_url = f"https://www.youtube.com/watch?v={video_id}"
        Path(OUTPUT_DIR).mkdir(parents=True, exist_ok=True)
        
        with open(file_path, 'w', encoding='utf-8') as f:
            # Başlık ve linki dosyaya ekleyelim
            f.write(f"Title: {title}\n")
            f.write(f"URL: {video_url}\n\n")
            f.write(srt_transcript)
        
        print(f"Saved transcript to {file_path}")
        return True
    return False

# Özet dosyasını yazma
def write_summary(succeeded, failed):
    with open(SUMMARY_FILE, 'w', encoding='utf-8') as f:
        f.write("Transkripti Başarıyla Alınan Videolar:\n")
        f.write("-------------------------------\n")
        for video in succeeded:
            f.write(f"Title: {video['title']}\n")
            f.write(f"URL: https://www.youtube.com/watch?v={video['videoId']}\n\n")
        
        f.write("\nTranskripti Alınamayan Videolar:\n")
        f.write("-------------------------------\n")
        for video in failed:
            f.write(f"Title: {video['title']}\n")
            f.write(f"URL: https://www.youtube.com/watch?v={video['videoId']}\n\n")
        print(f"Summary written to {SUMMARY_FILE}")

# Ana fonksiyon
def main():
    youtube = get_youtube_service()
    video_data = get_channel_video_ids(youtube, CHANNEL_ID)
    
    succeeded = []
    failed = []
    
    for video in video_data:
        transcript = get_video_transcript(video['videoId'])
        if save_transcript_to_file(video['videoId'], video['title'], transcript):
            succeeded.append(video)
        else:
            failed.append(video)
    
    write_summary(succeeded, failed)

if __name__ == '__main__':
    main()


Saved transcript to transcripts/fzFwFvo2o1Q.srt
Error retrieving transcript for video ukYElyDp5jk: 
Could not retrieve a transcript for the video https://www.youtube.com/watch?v=ukYElyDp5jk! This is most likely caused by:

Subtitles are disabled for this video

If you are sure that the described cause is not responsible for this error and that a transcript should be retrievable, please create an issue at https://github.com/jdepoix/youtube-transcript-api/issues. Please add which version of youtube_transcript_api you are using and provide the information needed to replicate the error. Also make sure that there are no open issues which already describe your problem!
Error retrieving transcript for video PXtsOdcjOMg: 
Could not retrieve a transcript for the video https://www.youtube.com/watch?v=PXtsOdcjOMg! This is most likely caused by:

Subtitles are disabled for this video

If you are sure that the described cause is not responsible for this error and that a transcript should be retriev

In [23]:
import os
import whisper
import yt_dlp
import ffmpeg

def check_ffmpeg():
    """ffmpeg ve ffprobe'nin yüklü olup olmadığını kontrol eder."""
    try:
        ffmpeg.probe('dummy', v='error')
        print("ffmpeg ve ffprobe yüklenmiş.")
    except ffmpeg.Error:
        raise RuntimeError("ffmpeg ve/veya ffprobe yüklenmemiş. Lütfen yükleyin.")

def download_audio(url, output_path):
    options = {
        'format': 'bestaudio/best',
        'outtmpl': output_path,
        'quiet': True,
        'postprocessors': [{
            'key': 'FFmpegExtractAudio',
            'preferredcodec': 'wav',
            'preferredquality': '192',
        }],
        'postprocessor_args': [
            '-ar', '16000'
        ]
    }
    with yt_dlp.YoutubeDL(options) as ydl:
        ydl.download([url])

def transcribe_audio(file_path, model):
    result = model.transcribe(file_path)
    return result['text']

def main(url_file, output_dir):
    # ffmpeg yüklenmiş mi kontrol et
    check_ffmpeg()

    # Whisper modelini yükle
    model = whisper.load_model("base", weights_only=True)

    # URL'leri dosyadan okuyun
    with open(url_file, 'r') as file:
        urls = file.readlines()

    # Çıkış dizini varsa oluşturun
    if not os.path.exists(output_dir):
        os.makedirs(output_dir)

    for url in urls:
        url = url.strip()
        if not url:
            continue
        try:
            video_id = url.split('=')[-1]  # Video ID'yi URL'den çıkarın
            audio_path = os.path.join(output_dir, f"{video_id}.wav")

            print(f"İndiriliyor: {url}")
            download_audio(url, audio_path)

            print(f"Transkripte ediliyor: {audio_path}")
            text = transcribe_audio(audio_path, model)
            print(f"Transkripti:\n{text}\n")

            # Geçici ses dosyasını temizleyin
            os.remove(audio_path)

        except Exception as e:
            print(f"Hata oluştu: {e}")

if __name__ == "__main__":
    url_file = 'video_urls.txt'  # Video URL'lerinin bulunduğu dosyanın yolu
    output_dir = 'downloads'  # İndirilen ses dosyalarının kaydedileceği dizin
    main(url_file, output_dir)


RuntimeError: ffmpeg ve/veya ffprobe yüklenmemiş. Lütfen yükleyin.

In [28]:
import subprocess
import yt_dlp
import whisper
import os

def check_ffmpeg():
    """ffmpeg ve ffprobe'nin yüklü olup olmadığını kontrol eder."""
    try:
        subprocess.run(['ffmpeg', '-version'], check=True, stdout=subprocess.PIPE, stderr=subprocess.PIPE)
        subprocess.run(['ffprobe', '-version'], check=True, stdout=subprocess.PIPE, stderr=subprocess.PIPE)
        print("ffmpeg ve ffprobe yüklenmiş.")
    except subprocess.CalledProcessError:
        raise RuntimeError("ffmpeg ve/veya ffprobe yüklenmemiş. Lütfen yükleyin.")
    except FileNotFoundError:
        raise RuntimeError("ffmpeg ve/veya ffprobe bulunamadı. Lütfen PATH'e ekleyin.")

def download_audio(video_url, output_dir):
    """Verilen URL'den ses dosyasını indirir."""
    ydl_opts = {
        'format': 'bestaudio/best',
        'outtmpl': os.path.join(output_dir, '%(title)s.%(ext)s'),
        'noplaylist': True,
        'postprocessors': [{
            'key': 'FFmpegExtractAudio',
            'preferredcodec': 'mp3',
            'preferredquality': '192',
        }],
        'postprocessor_args': [
            '-ar', '16000'
        ],
        'prefer_ffmpeg': True,
    }
    with yt_dlp.YoutubeDL(ydl_opts) as ydl:
        ydl.download([video_url])

def transcribe_audio(audio_path, model):
    """Ses dosyasını transkripte eder."""
    result = model.transcribe(audio_path)
    return result['text']

def process_videos(url_file, output_dir):
    """URL dosyasından video URL'lerini okuyup sesleri indirir ve transkripte eder."""
    check_ffmpeg()
    
    if not os.path.exists(output_dir):
        os.makedirs(output_dir)
    
    # Whisper modelini yükle
    model = whisper.load_model("base")
    
    with open(url_file, 'r') as file:
        urls = file.readlines()
    
    for url in urls:
        url = url.strip()
        if url:
            try:
                print(f"İndiriliyor: {url}")
                download_audio(url, output_dir)
                
                audio_files = [f for f in os.listdir(output_dir) if f.endswith('.mp3')]
                for audio_file in audio_files:
                    audio_path = os.path.join(output_dir, audio_file)
                    print(f"Transkripte ediliyor: {audio_path}")
                    transcript = transcribe_audio(audio_path, model)
                    print(f"Transkript: {transcript}")
                    
                    # Transkripti bir dosyaya kaydet
                    transcript_file = os.path.splitext(audio_file)[0] + '.txt'
                    with open(os.path.join(output_dir, transcript_file), 'w') as f:
                        f.write(transcript)
            except Exception as e:
                print(f"Bir hata oluştu: {e}")

# Örnek kullanım
url_file = 'video_urls.txt'  # Video URL'lerinin bulunduğu dosyanın yolu
output_dir = 'downloads'  # İndirilen ses dosyalarının kaydedileceği dizin
process_videos(url_file, output_dir)


ffmpeg ve ffprobe yüklenmiş.


/Users/taha/Desktop/rag/venv/lib/python3.12/site-packages/whisper/__init__.py:146: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(fp, map_location=dev

İndiriliyor: https://www.youtube.com/watch?v=fzFwFvo2o1Q
[youtube] Extracting URL: https://www.youtube.com/watch?v=fzFwFvo2o1Q
[youtube] fzFwFvo2o1Q: Downloading webpage
[youtube] fzFwFvo2o1Q: Downloading ios player API JSON
[youtube] fzFwFvo2o1Q: Downloading web creator player API JSON
[youtube] fzFwFvo2o1Q: Downloading m3u8 information
[info] fzFwFvo2o1Q: Downloading 1 format(s): 251
[download] Destination: downloads/MagentaTV statt Kabel-TV - Was der Wegfall des Nebenkostenprivilegs für dich bedeutet!.webm
[download] 100% of    1.78MiB in 00:00:00 at 3.06MiB/s   
[ExtractAudio] Destination: downloads/MagentaTV statt Kabel-TV - Was der Wegfall des Nebenkostenprivilegs für dich bedeutet!.mp3
Deleting original file downloads/MagentaTV statt Kabel-TV - Was der Wegfall des Nebenkostenprivilegs für dich bedeutet!.webm (pass -k to keep)
Transkripte ediliyor: downloads/MagentaTV statt Kabel-TV - Was der Wegfall des Nebenkostenprivilegs für dich bedeutet!.mp3


/Users/taha/Desktop/rag/venv/lib/python3.12/site-packages/whisper/transcribe.py:115: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")


Transkript:  Hey, das Nebenkosten frübeligen Fett. Hey, denkst du? Und was interessiert mich das? Als Mieter und Nutze eines Kabelfernseheranschlusses interessiert sich auf jeden Fall, weil du profitierst davon. Als Mieter zahlst du oft die Kosten für deinen Kabelteferanschluss über die Nebenkosten, ob du diesen Nutzt oder nicht. Check doch einfach mal deine jährliche Nebenkostenabrechnung und guck ob und wie viel du bezahlst. Die gute Nachricht ist, diese Pflicht entfällt ab dem 1.07.2024. Ab dann hast du endlich die freiwaal einen für dich passenden TV-Tarif auszurellen. Das bedeutet in jedem Fall du behaust einen neuen TV-Vertrag. Ansonsten kann es dir passieren, dass ein bisheriger Kabel TV-Unbieter abschaltet und du ohne Fernseh darstäst. Den bisherigen Kabel TV-Anbieter brauchst du nicht kündigen, die Umlage entfällt automatisch. Und noch eine gute Nachricht. Es lohnt sich heute schon, sich zu informieren und zu magenta TV zu wechseln. Fernseh und Streaming-Enhalte sind bei uns g

...

/Users/taha/Desktop/rag/venv/lib/python3.12/site-packages/whisper/transcribe.py:115: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")


Transkript:  Hey, das Nebenkosten frübeligen Fett. Hey, denkst du? Und was interessiert mich das? Als Mieter und Nutze eines Kabelfernseheranschlusses interessiert sich auf jeden Fall, weil du profitierst davon. Als Mieter zahlst du oft die Kosten für deinen Kabelteferanschluss über die Nebenkosten, ob du diesen Nutzt oder nicht. Check doch einfach mal deine jährliche Nebenkostenabrechnung und guck ob und wie viel du bezahlst. Die gute Nachricht ist, diese Pflicht entfällt ab dem 1.07.2024. Ab dann hast du endlich die freiwaal einen für dich passenden TV-Tarif auszurellen. Das bedeutet in jedem Fall du behaust einen neuen TV-Vertrag. Ansonsten kann es dir passieren, dass ein bisheriger Kabel TV-Unbieter abschaltet und du ohne Fernseh darstäst. Den bisherigen Kabel TV-Anbieter brauchst du nicht kündigen, die Umlage entfällt automatisch. Und noch eine gute Nachricht. Es lohnt sich heute schon, sich zu informieren und zu magenta TV zu wechseln. Fernseh und Streaming-Enhalte sind bei uns g

/Users/taha/Desktop/rag/venv/lib/python3.12/site-packages/whisper/transcribe.py:115: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")


Transkript:  Ich habe unsere Geräte gefunden, wie ihr da das von der Telekom kommen lassen. Wir waren doch letzte Woche hier und haben zusammen die Leitungs-ID ausgelesen. Ja, stimmt. Wir waren letzte Woche hier, haben den Router mit der Telefondose verbunden. Ich habe mich damit mit meinem Handy in das WLAN eingelockt und bin auf diese Seite gegangen. Hab die Leitungs-ID herausgefunden und die dann in der Telekom geschickt. Dafür brauchst du nur deinen Router mit den Zetteln und dein Smartphone mit dem Mein Margente-App. Nachdem du die Mein Margente-App öffnest und auf Service gehst, Internet zu Hause und auf Internet einrichten. So, jetzt erst mal das Gerät auswählen, den Tarif, dann optimal den Router ausrichten und jetzt DSL und Stromkabel verbinden. Easy. Und natürlich unser Speedphone nicht vergessen. Ist du noch schnell den QR-Codes gehen? Und schon sind wir online. Ja, das war super einfach. Es läuft jetzt auch alles. Hier hast du jetzt unsere Nummer. Wir sehen uns. Habt ihr di

/Users/taha/Desktop/rag/venv/lib/python3.12/site-packages/whisper/transcribe.py:115: UserWarning: FP16 is not supported on CPU; using FP32 instead
  warnings.warn("FP16 is not supported on CPU; using FP32 instead")
